In [1]:
import numpy as np
import pandas as pd
from os.path import join as pjoin

import bokeh

In [2]:
from bokeh.plotting import figure
from bokeh.layouts import column
from bokeh.models.widgets import Panel, Tabs
from bokeh.io import output_notebook, show, output_file, reset_output, gridplot, save

reset_output()
output_notebook()

Loading BokehJS ...

In [3]:
working_directory = "/home/alex/Documents/Projet_info/Deep-Reinforcement-Learning/callbacks"
n_actors = 8
n_plot = 5
list_files = ["rpe.csv", "rewards.csv", "random.csv", "diff.csv", "action.csv"]
list_titles = ["Reward per Environment", "Reward per Iteration", "Randomness","Norm of applied gradients", "gnActions taken"]
list_x_labels = ["Environments", "Iterations", "Iterations", "Iterations", "Iterations"]
list_y_labels = ["Reward", "Reward", "Random ?", "Norm", "Action"]
colors = ["orange", "lime", "navy", "darkred", "purple"]


In [4]:
reset_output()
output_notebook()

tabs = []
p = []
for j in range(n_actors):
    p.append([])
    for i in range(n_plot):
        data = pd.read_csv(pjoin(working_directory, "actor"+str(j), list_files[i]), header=None, names=["to_plot"])
        if i in [2, 4]:
            data["data"] = data["to_plot"].values
            data["to_plot"] = np.convolve(data.data, np.ones((100,))/100, mode='same')
        p[j].append(figure(title=list_titles[i], width=900, height=350))
        p[j][i].grid.grid_line_alpha = 0
        p[j][i].xaxis.axis_label = list_x_labels[i]
        p[j][i].yaxis.axis_label = list_y_labels[i]
        p[j][i].ygrid.band_fill_color = "olive"
        p[j][i].ygrid.band_fill_alpha = 0.1

        p[j][i].line(data.index, data["to_plot"], color=colors[i])
    
    tabs.append(Panel(child=column(p[j]), title="actor"+str(j)))

tabs_f = Tabs(tabs=tabs)
show(tabs_f)

Loading BokehJS ...

In [5]:
data = pd.read_csv(pjoin(working_directory, "actor0", "history.csv"), header=None, names=["times", "true", 
                "estimated"], sep=";", index_col=False)

data["indic"] = np.cumsum((data.times == 0).astype(np.int16))

p=(figure(title="History", width=900, height=350))
p.grid.grid_line_alpha = 0
p.xaxis.axis_label = "times"
p.yaxis.axis_label = "Rewards"
p.ygrid.band_fill_color = "olive"
p.ygrid.band_fill_alpha = 0.1

true = []
for i in np.unique(data["indic"]):
    pseudo_true = data[data.indic == i]["true"].values[::-1]
    true_temp = [pseudo_true[0]]
    for j in range(1, len(pseudo_true)):
        true_temp.append(pseudo_true[j] + 0.9 * true_temp[j-1])
    true.append(np.array(true_temp)[::-1])
    p.line(data[data.indic == i]["times"], true[i-1], color="lime")
    p.line(data[data.indic == i]["times"], data[data.indic == i]["estimated"], color="red")
    
show(p)

In [6]:
from bokeh.layouts import row, widgetbox
from bokeh.models import CustomJS, Slider
from bokeh.plotting import figure, output_file, show, ColumnDataSource

x = np.linspace(0, 10, 500)
y = np.sin(x)

source = ColumnDataSource(data=dict(x=x, y=y))

plot = figure(y_range=(-10, 10), plot_width=400, plot_height=400)

plot.line('x', 'y', source=source, line_width=3, line_alpha=0.6)

callback = CustomJS(args=dict(source=source), code="""
    var data = source.data;
    var A = amp.value;
    var k = freq.value;
    var phi = phase.value;
    var B = offset.value;
    x = data['x']
    y = data['y']
    for (i = 0; i < x.length; i++) {
        y[i] = B + A*Math.sin(k*x[i]+phi);
    }
    source.trigger('change');
""")

amp_slider = Slider(start=0.1, end=10, value=1, step=.1,
                    title="Amplitude", callback=callback)
callback.args["amp"] = amp_slider

freq_slider = Slider(start=0.1, end=10, value=1, step=.1,
                     title="Frequency", callback=callback)
callback.args["freq"] = freq_slider

phase_slider = Slider(start=0, end=6.4, value=0, step=.1,
                      title="Phase", callback=callback)
callback.args["phase"] = phase_slider

offset_slider = Slider(start=-5, end=5, value=0, step=.1,
                       title="Offset", callback=callback)
callback.args["offset"] = offset_slider

layout = row(
    plot,
    widgetbox(amp_slider, freq_slider, phase_slider, offset_slider),
)

output_file("slider.html", title="slider.py example")

show(layout)

64.0
